In [3]:
import math
import hazm
import parsivar
import re
from Tokenizer import Tokenizer
from Normalizer import Normalizer

In [4]:
import json
with open('IR_data_news_5k.json', 'r', encoding='utf-8') as file:
    data = json.load(file)


In [5]:
item_keys = list(data.keys())
News_items = {}
url = {}
for i in item_keys:
    item_value = data[i]
    key = (f'Key: {i}')
    value = (f'Value: {item_value}')
    content = (f'Content: {item_value["content"]}')
    url_news = (f'url: {item_value["url"]}')
    print(key,content)
    News_items[key] = content
    url[key] = url_news

Key: 4092 Content: 
به گزارش خبرگزاری فارس، سردار آزمون ستاره تیم ملی کشورمان و عضو باشگاه زنیت به دلیل درخشش بی نظیرش در لیگ روسیه و نزدیک بودن زمان پایان قراردادش با باشگاه روسی مشتریان زیادی پیدا کرده است. سیماک سرمربی زنیت روز گذشته در مصاحبه با رسانه های روسیه اعلام کرد مسئله آینده آزمون آسان است این بازیکن قصد تمدید قراردادش را ندارد و در تابستان به باشگاه جدیدی می رود. در همین رابطه سایت «hitc» به تحلیل حرف های سرمربی زنیت پرداخت و این حرف ها را فرصتی استثنایی برای دو باشگاه اورتون و نیوکاسل دانست.  این رسانه انگلیسی، نوشت: سردار آزمون ستاره ایرانی زنیت در لیگ قهرمانان اروپا در یک بازی جذاب به کابوس هواداران چلسی تبدیل شد. این ستاره ایرانی یک گل فوق العاده در این بازی به ثمر رساند و اگر واکنش های فوق العاده کپه آ نبود می توانست چندین بار دیگر دروزاه شاگردان توخل را باز کند. ستاره ایرانی از دو سال گذشته بنا به اعلام مدیر برنامه اش از باشگاه اورتون با ریاست فرهاد مشیری ایرانی پیشنهاد داشته و یکی از گزینه های تقویت خط حمله این تیم است. از طرف دیگر نیوکاسل که در آستانه سقوط قرار دار

In [6]:
tokenizer = Tokenizer()
normalizer = Normalizer()
stemmer = parsivar.FindStems()

In [7]:

def remove_punctuation(text):
    punctuation = '''!()-[]{};:'"\,<>./?@#$%^&*_~،٫٬!‍‌()=+|[]{}»«:؛؟'''
    no_punctuation = ""
    for char in text:
        if char not in punctuation:
            no_punctuation = no_punctuation + char
    return no_punctuation

In [8]:
def remove_line_half(text):
    no_line = ""
    for char in text:
        if char != '\n' and char != '\r':
            no_line = no_line + char
    return no_line

In [9]:
def create_positional_dictionary(text,docID,positional_dictionary):
    #each key should have the total number of occurences of the word in the document
    #each value should be a list of the positions of the word in the document
    text = remove_punctuation(text)
    text = remove_line_half(text)
    text = normalizer.normalize(text)
    words = tokenizer.tokenize(text)
    for i in range(len(words)):
        words[i] = stemmer.convert_to_stem(words[i])
        if words[i] not in positional_dictionary.keys():
            positional_dictionary[words[i]] = [1,{docID:[1,[i]]}]
        else:
            positional_dictionary[words[i]][0] += 1
            if docID not in positional_dictionary[words[i]][1].keys():
                positional_dictionary[words[i]][1][docID] = [1,[i]]
            else:
                positional_dictionary[words[i]][1][docID][0] += 1
                positional_dictionary[words[i]][1][docID][1].append(i)
    return positional_dictionary
    

In [10]:
def merge_positional_dictionaries(dict1, dict2):
    #merge two positional dictionaries
    #if a word appears in both dictionaries, the positions should be merged
    #the total number of occurences should be updated
    for key in dict2.keys():
        if key not in dict1.keys():
            dict1[key] = dict2[key]
        else:
            dict1[key][0] += dict2[key][0]
            dict1[key][1] += dict2[key][1]
    return dict1

In [11]:
index = []
dictionary = {}
for i in item_keys:
    content = data[i]['content']
    dictionary = create_positional_dictionary(content,int(i),dictionary)

In [12]:
#find the top 50 words with the highest frequency
top_50 = []
for i in range(50):
    max = 0
    max_key = ""
    for key in dictionary.keys():
        if dictionary[key][0] > max:
            max = dictionary[key][0]
            max_key = key
    top_50.append([max_key,max])
    del dictionary[max_key]

In [13]:
def add_tf_idf(dictionary):
    #add tf-idf to the positional dictionary for each word in each document
    #tf = 1 + log10(tf)
    #idf = log10(N/df)
    #tf-idf = tf * idf
    N = len(item_keys)
    for key in dictionary.keys():
        for docID in dictionary[key][1].keys():
            tf = 1 + math.log10(dictionary[key][1][docID][0])
            #idf is the number of documents that contain the word
            idf = math.log10(N/len(dictionary[key][1]))
            tf_idf = tf * idf
            dictionary[key][1][docID].append(tf_idf)
            #store length of the vector for each document
    return dictionary

In [14]:
def calc_doc_vector_length(dictionary):
    #calculate the length of the vector for each document
    #this is used for cosine similarity
    length = {}
    for key in dictionary.keys():
        for docID in dictionary[key][1].keys():
            if docID not in length.keys():
                length[docID] = dictionary[key][1][docID][2] ** 2
            else:
                length[docID] += dictionary[key][1][docID][2] ** 2
    for docID in length.keys():
        length[docID] = math.sqrt(length[docID])
    return length

In [15]:
dictionary = add_tf_idf(dictionary)
length = calc_doc_vector_length(dictionary)

In [16]:
import pickle
with open('dictionary.pickle', 'wb') as handle:
    pickle.dump(dictionary, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [17]:
#show sample of the positional dictionary
sample = {}
for key in dictionary.keys():
    sample[key] = dictionary[key]
    if len(sample) == 5:
        break

In [18]:
def cosine_similarity(dictionary,vector_query,k,length):
    top_k = []
    similar = {}
    vector_length = 0
    for key in vector_query.keys():
        vector_length += vector_query[key] * vector_query[key]
    vector_length = math.sqrt(vector_length)
    for key in vector_query.keys():
        if key not in dictionary.keys():
            continue
        for doc in dictionary[key][1]:
            if doc not in similar.keys():
                similar[doc] = 0
            similar[doc] += (vector_query[key] * dictionary[key][1][doc][2]) / (length[doc] * vector_length)
    for i in range(k):
        max = 0
        max_key = ""
        for key in similar.keys():
            if similar[key] > max:
                max = similar[key]
                max_key = key
        top_k.append(max_key)
        if max_key != "":
            del similar[max_key]
        else:
            break
    return top_k

In [19]:
def tf_idf_query_calc(dictionary,query):
    query = remove_punctuation(query)
    query = remove_line_half(query)
    query = normalizer.normalize(query)
    query_words = tokenizer.tokenize(query)
    for i in range(len(query_words)):
        query_words[i] = stemmer.convert_to_stem(query_words[i])
    vector_query = {}
    for word in query_words:
        if word not in vector_query.keys():
            vector_query[word] = 1
        else:
            vector_query[word] += 1
    #calculate the tf-idf of the query
    N = len(item_keys)
    for word in vector_query.keys():
        if word not in dictionary.keys():
            vector_query[word] = 0
            continue
        tf = 1 + math.log10(vector_query[word])
        idf = math.log10(N/dictionary[word][0])
        tf_idf = tf * idf
        vector_query[word] = tf_idf
    return vector_query

In [20]:
def create_champion_list(dictionary,k):
    #create a champion list of the top k documents for each word
    #the champion list should be a dictionary with the word as the key
    #the value should be a list of the top k documents for that word
    champion_list = {}
    for key in dictionary.keys():
        champion_list[key] = dictionary[key]
    return champion_list

In [21]:
k = 20
champion_list = create_champion_list(dictionary,k)

In [22]:
def search_query(query,champion_list_use=False,k=5):
    if champion_list_use == True:
        dictionary_use = champion_list
    else:
        dictionary_use = dictionary
    top_k = (cosine_similarity(dictionary=dictionary_use,vector_query=tf_idf_query_calc(dictionary=dictionary,query=query),k=k,length=length))
    for i in top_k:
        if i != "":
            #print the title of the document
            print(data[str(i)]['title'])
            #print the sentence of the document that contains the query
            print(i,News_items[f'Key: {i}'])
            print(i,url[f'Key: {i}'])

In [24]:
#time of using champion list and not using champion list
query = input("Query: ")
import time
start = time.time()
search_query(query=query,champion_list_use=False)
end = time.time()
print(end - start)

«مسی2» در فوتبال جنجال آفرین شد+عکس
2367 Content: 
به گزارش خبرگزاری فارس، فوتبال آرژانتین شاهد ظهور بازیکنی به نام خواکین «مسی» است. خواکین روز گذشته برای اولین بار برای تیم نیولز اولد بویز وارد زمین بازی شد و با پیراهن «مسی» بازی کرد. این اقدام بازیکن جوان آرژانتینی در میان هواداران فوتبال این کشور باعث اختلاف شد. بسیاری از هواداران تیم ملی آرژانتین از این بازیکن جوان خواستند تا سریعا نام  «مسی» را از روی پیراهنش پاک کند چون این نام تنها برای لیونل مسی اسطوره فوتبال این کشور است.  مسی هم از این باشگاه آرژانتینی فوتبالش را آغاز کرده بود و با این تیم به دنیای فوتبال حرفه ای معرفی شد. این بازیکن جوان درباره اینکه آیا با مسی فامیل است این طور پاسخ داد: بسیاری از مردم درباره فامیلی من با مسی سوال می کنند اما من نسبتی با مسی ندارم بلکه از روی تصادف، فامیلی ما یکی است. اسطوره فوتبال آرژانتین با 7 توپ طلای بهترین بازیکن جهان یکی از بازیکنان ماندگار مستطیل سبز است به همین خاطر هواداران فوتبال خواهان تغییر نام این بازیکن جوان شدند تا برند مسی حفظ شود. انتهای پیام/



2367 url: https://www.fars